In [ ]:
from google.colab import drive
drive.mount('/content/drive')

import zipfile
import os
import pandas as pd
import numpy as np
import tensorflow as tf
from music21 import converter, note, stream
from sklearn.model_selection import train_test_split
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout
from tensorflow.keras.callbacks import ModelCheckpoint

# Extract EMOPIA dataset
zip_path = "/content/drive/My Drive/EMOPIA_1.0.zip"
extract_path = "/content/EMOPIA"
with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(extract_path)
print("Dataset extracted to:", extract_path)

# Paths to dataset files
dataset_path = "/content/EMOPIA/EMOPIA_1.0"
midi_path = os.path.join(dataset_path, "midis")
label_csv_path = os.path.join(dataset_path, "label.csv")

# Load labels
labels_df = pd.read_csv(label_csv_path)
labels_df.columns = labels_df.columns.str.strip()  # Remove whitespace
labels_df['emotion'] = labels_df['4Q'].apply(lambda q: "happy" if q in [1, 4] else "sad")

# Filter only happy music
happy_df = labels_df[labels_df['emotion'] == 'happy']

# Function to extract notes from a MIDI file
def extract_notes(file_path):
    midi_stream = converter.parse(file_path)
    notes = []
    for element in midi_stream.flatten().notes:
        if isinstance(element, note.Note):
            notes.append(str(element.pitch))
        elif isinstance(element, note.Rest):
            notes.append('rest')
    return notes

# Extract notes from happy MIDI files
all_notes = []
for midi_file in os.listdir(midi_path):
    if midi_file.endswith('.mid'):
        file_id = midi_file.split('.')[0]
        if file_id in happy_df['ID'].values:
            file_path = os.path.join(midi_path, midi_file)
            notes = extract_notes(file_path)
            all_notes.append(notes)

# Create mappings and prepare sequences
unique_notes = sorted(set(note for notes in all_notes for note in notes))
note_to_int = {note: i for i, note in enumerate(unique_notes)}
sequence_length = 100

# Convert notes to sequences
network_input = []
for notes in all_notes:
    for i in range(len(notes) - sequence_length):
        network_input.append([note_to_int[note] for note in notes[i:i + sequence_length]])

# Prepare data for LSTM
X = np.array(network_input)
X = np.reshape(X, (X.shape[0], sequence_length, 1)) / float(len(unique_notes))
y = np.array([note_to_int[notes[i + sequence_length]] for notes in all_notes for i in range(len(notes) - sequence_length)])
y = tf.keras.utils.to_categorical(y, num_classes=len(unique_notes))

# Train-test split
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

# Define LSTM model
model = Sequential([
    LSTM(256, input_shape=(X.shape[1], X.shape[2]), return_sequences=True),
    Dropout(0.3),
    LSTM(256),
    Dropout(0.3),
    Dense(len(unique_notes), activation='softmax')
])
model.compile(loss='categorical_crossentropy', optimizer='adam')
model.summary()

# Save best model during training
checkpoint = ModelCheckpoint(
    "/content/drive/My Drive/emopia_project/happy_model.keras",
    save_best_only=True,
    save_weights_only=False,
    verbose=1
)

# Train model
history = model.fit(
    X_train, y_train,
    validation_data=(X_val, y_val),
    epochs=10,
    batch_size=64,
    callbacks=[checkpoint]
)

print("Happy model training complete!")


Mounted at /content/drive
Dataset extracted to: /content/EMOPIA


/usr/local/lib/python3.11/dist-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ lstm (LSTM)                          │ (None, 100, 256)            │         264,192 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout (Dropout)                    │ (None, 100, 256)            │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm_1 (LSTM)                        │ (None, 256)                 │         525,312 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_1 (Dropout)                  │ (None, 256)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 83)                  │          21,331 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 810,835 (3.09 MB)

 Trainable params: 810,835 (3.09 MB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 4.0029
Epoch 1: val_loss improved from inf to 3.86807, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 ━━━━━━━━━━━━━━━━━━━━ 625s 1s/step - loss: 4.0028 - val_loss: 3.8681
Epoch 2/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 3.8953
Epoch 2: val_loss improved from 3.86807 to 3.85076, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 ━━━━━━━━━━━━━━━━━━━━ 602s 1s/step - loss: 3.8953 - val_loss: 3.8508
Epoch 3/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 3.8591
Epoch 3: val_loss improved from 3.85076 to 3.83634, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 ━━━━━━━━━━━━━━━━━━━━ 629s 1s/step - loss: 3.8591 - val_loss: 3.8363
Epoch 4/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 3.8323
Epoch 4: val_loss improved from 3.83634 to 3.82882, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 ━━━━

In [ ]:
from keras.callbacks import EarlyStopping

early_stopping = EarlyStopping(
    monitor='val_loss',
    patience=3,  # Stop training if val_loss doesn't improve for 3 consecutive epochs
    restore_best_weights=True
)

model.fit(
    X_train, y_train,
    epochs=10,
    batch_size=64,
    validation_data=(X_val, y_val),
    callbacks=[early_stopping, checkpoint]
)


Epoch 1/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 3.5084
Epoch 1: val_loss improved from 3.55871 to 3.47844, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 ━━━━━━━━━━━━━━━━━━━━ 606s 1s/step - loss: 3.5084 - val_loss: 3.4784
Epoch 2/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 3.4329
Epoch 2: val_loss improved from 3.47844 to 3.43831, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 ━━━━━━━━━━━━━━━━━━━━ 632s 1s/step - loss: 3.4329 - val_loss: 3.4383
Epoch 3/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 3.3713
Epoch 3: val_loss improved from 3.43831 to 3.41776, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 ━━━━━━━━━━━━━━━━━━━━ 611s 1s/step - loss: 3.3713 - val_loss: 3.4178
Epoch 4/10
491/491 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - loss: 3.3288
Epoch 4: val_loss improved from 3.41776 to 3.35128, saving model to /content/drive/My Drive/emopia_project/happy_model.keras
491/491 

In [ ]:
from keras.models import load_model

# Load the saved happy model
happy_model_path = "/content/drive/My Drive/emopia_project/happy_model.keras"
happy_model = load_model(happy_model_path)
print("Happy model loaded successfully!")


Happy model loaded successfully!


In [ ]:
# Recreate dataset preparation
dataset_path = "/content/EMOPIA/EMOPIA_1.0"
midi_path = os.path.join(dataset_path, "midis")
label_csv_path = os.path.join(dataset_path, "label.csv")

# Load labels
labels_df = pd.read_csv(label_csv_path)
labels_df.columns = labels_df.columns.str.strip()
labels_df['emotion'] = labels_df['4Q'].apply(lambda q: "happy" if q in [1, 4] else "sad")

# Filter only happy music
happy_df = labels_df[labels_df['emotion'] == 'happy']

# Function to extract notes from a MIDI file
def extract_notes(file_path):
    midi_stream = converter.parse(file_path)
    notes = []
    for element in midi_stream.flatten().notes:
        if isinstance(element, note.Note):
            notes.append(str(element.pitch))
        elif isinstance(element, note.Rest):
            notes.append('rest')
    return notes

# Extract notes from happy MIDI files
all_notes = []
for midi_file in os.listdir(midi_path):
    if midi_file.endswith('.mid'):
        file_id = midi_file.split('.')[0]
        if file_id in happy_df['ID'].values:
            file_path = os.path.join(midi_path, midi_file)
            notes = extract_notes(file_path)
            all_notes.append(notes)

# Create mappings and prepare sequences
unique_notes = sorted(set(note for notes in all_notes for note in notes))
note_to_int = {note: i for i, note in enumerate(unique_notes)}
sequence_length = 100

# Convert notes to sequences
network_input = []
for notes in all_notes:
    for i in range(len(notes) - sequence_length):
        network_input.append([note_to_int[note] for note in notes[i:i + sequence_length]])

# Prepare data for LSTM
X = np.array(network_input)
X = np.reshape(X, (X.shape[0], sequence_length, 1)) / float(len(unique_notes))
y = np.array([note_to_int[notes[i + sequence_length]] for notes in all_notes for i in range(len(notes) - sequence_length)])
y = tf.keras.utils.to_categorical(y, num_classes=len(unique_notes))

# Recreate train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

print("Data is ready for testing!")
print(f"Train samples: {len(X_train)}, Test samples: {len(X_test)}")


Data is ready for testing!
Train samples: 31381, Test samples: 7846


In [ ]:
import numpy as np

# Select a random sequence from X_test
seed_index = np.random.randint(0, len(X_test))
seed_sequence = X_test[seed_index]  # This will have shape (sequence_length, 1)

print("Seed sequence selected successfully!")


Seed sequence selected successfully!


In [ ]:
import numpy as np

# Adjust the temperature value (higher = more randomness, lower = more deterministic)
temperature = 1.0

def sample_with_temperature(predicted_probs, temperature):
    predicted_probs = np.log(predicted_probs + 1e-10) / temperature
    predicted_probs = np.exp(predicted_probs) / np.sum(np.exp(predicted_probs))
    return np.random.choice(len(predicted_probs), p=predicted_probs)

generated_notes = []
current_sequence = seed_sequence

for _ in range(100):  # Generate 100 notes
    current_sequence = np.reshape(current_sequence, (1, sequence_length, 1))
    current_sequence = current_sequence / float(len(unique_notes))  # Normalize

    # Predict the next note with temperature sampling
    predicted_probs = model.predict(current_sequence, verbose=0)[0]
    predicted_note_int = sample_with_temperature(predicted_probs, temperature)

    # Append the predicted note
    generated_notes.append(predicted_note_int)

    # Update the sequence
    current_sequence = np.append(current_sequence[0, 1:], [[predicted_note_int]], axis=0)

# Convert generated notes back to note names
generated_notes_names = [unique_notes[note_int] for note_int in generated_notes]
print("Generated notes:", generated_notes_names)


Generated notes: ['A2', 'A1', 'C#5', 'A2', 'E3', 'A1', 'A3', 'A2', 'D3', 'B3', 'A1', 'A3', 'A2', 'E4', 'B4', 'B3', 'A3', 'A4', 'A3', 'A2', 'A2', 'E3', 'A2', 'A2', 'A4', 'A2', 'A3', 'A1', 'A3', 'A2', 'A2', 'E2', 'A2', 'A4', 'E5', 'B-3', 'A3', 'B-5', 'A2', 'A1', 'A2', 'A2', 'A2', 'B4', 'A2', 'A3', 'A3', 'A2', 'E4', 'A2', 'A1', 'A3', 'A2', 'A1', 'E4', 'C#5', 'A4', 'A2', 'A2', 'A2', 'A2', 'C#5', 'A4', 'A2', 'A2', 'A2', 'A2', 'G1', 'C#3', 'B1', 'A2', 'A2', 'A2', 'A2', 'A2', 'A2', 'A3', 'A2', 'A4', 'A4', 'F#3', 'A4', 'A3', 'C#4', 'F#4', 'A2', 'A2', 'A2', 'A3', 'A3', 'C#5', 'A2', 'A1', 'A2', 'A2', 'A3', 'A1', 'A2', 'A2', 'A2']


In [ ]:
from music21 import stream, note, midi

# Create a music21 Stream
output_stream = stream.Stream()

for n in generated_notes_names:
    if n == "rest":  # Handle rests
        new_note = note.Rest()
    else:  # Handle pitched notes
        new_note = note.Note(n)
        new_note.quarterLength = 0.5  # Set the duration of each note (adjust as needed)

    output_stream.append(new_note)

# Save the Stream to a MIDI file
output_midi_path = "/content/Generated_Happy_Music.mid"
output_stream.write("midi", fp=output_midi_path)

print(f"MIDI file created: {output_midi_path}")


MIDI file created: /content/Generated_Happy_Music.mid


In [ ]:
from IPython.display import Audio

# Use the MIDI file to generate sound
!apt-get install -y timidity  # Install timidity if not already installed
!timidity {output_midi_path} -Ow -o output.wav
Audio("output.wav")


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following additional packages will be installed:
  fluid-soundfont-gm libao-common libao4
Suggested packages:
  fluid-soundfont-gs libaudio2 libsndio6.1 freepats pmidi timidity-daemon
The following NEW packages will be installed:
  fluid-soundfont-gm libao-common libao4 timidity
0 upgraded, 4 newly installed, 0 to remove and 49 not upgraded.
Need to get 130 MB of archives.
After this operation, 151 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 fluid-soundfont-gm all 3.1-5.3 [130 MB]
Get:2 http://archive.ubuntu.com/ubuntu jammy/main amd64 libao-common all 1.2.2+20180113-1.1ubuntu3 [6,568 B]
Get:3 http://archive.ubuntu.com/ubuntu jammy/main amd64 libao4 amd64 1.2.2+20180113-1.1ubuntu3 [35.2 kB]
Get:4 http://archive.ubuntu.com/ubuntu jammy-updates/universe amd64 timidity amd64 2.14.0-8ubuntu1.22.04.1 [681 kB]
Fetched 130 MB in 3s (44.